# Setup

Classic notebook setup

In [1]:
# Automatically reloads modules before executing code.
# This ensures that any changes made to imported Python files (e.g. .py modules) 
# are reflected in the notebook without needing to restart the kernel.

%load_ext autoreload
%autoreload 2

In [2]:
import os
import sys
import time
import numpy as np
from scipy.stats import norm
import matplotlib.pyplot as plt
from samplers.rejection_sampler import *

In [54]:
# For animations
%matplotlib notebook
from IPython.display import HTML

# What is a rejection sampler?

Rejection sampling is a simple but powerful algorithm for generating samples from a target probability distribution \\( p(x) \\), when direct sampling is difficult.

The idea is to use an easier-to-sample *proposal distribution* \\( q(x) \\), and accept or reject proposed samples based on how well \\( q(x) \\) covers \\( p(x) \\).

The algorithm requires:

- A proposal distribution \\( q(x) \\) such that \\( q(x) > 0 \\) whenever \\( p(x) > 0 \\).
- A constant \\( M \geq 1 \\) satisfying \\( p(x) \leq M q(x) \\) for all \\( x \\).

The procedure is:

1️⃣ **Sample \\( x \sim q(x) \\).**  
2️⃣ **Sample \\( u \sim \mathcal{U}(0,1) \\).**  
3️⃣ **Accept \\( x \\) if \\( u \leq \frac{p(x)}{M q(x)} \\); otherwise reject it.**

Accepted samples follow the target distribution \\( p(x) \\).

🔑 **Key points:**  

- The choice of \\( q(x) \\) and \\( M \\) affects the efficiency (acceptance rate).  
- A good proposal distribution closely matches the shape of \\( p(x) \\).  
- The acceptance rate is \\( 1 / M \\) on average.

In this notebook, we demonstrate rejection sampling on various distributions (Gaussian, multimodal, multivariate) and analyze the impact of the proposal distribution and the value of \\( M \\).


In [64]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation

# Target: standard Gaussian
def p(x):
    return (1 / np.sqrt(2 * np.pi)) * np.exp(-0.5 * x**2)

# Proposal: uniform on [-4,4]
def q(x):
    return np.where((x<4) & (x>-4), 1/8, 0)

# M chosen so that p(x) <= M q(x)
M = p(0) / q(0)  # p(0)=1/sqrt(2pi), q(0)=1/8

# Precompute proposal density line
x_vals = np.linspace(-5, 5, 500)
p_vals = p(x_vals)
q_vals = q(x_vals)


fig, ax = plt.subplots(figsize=(8, 6))
# Data for the animation
proposed_x = []
proposed_y = []
face_colors = []
scat = ax.scatter([], [])

def init():
    ax.fill_between(x_vals, x_vals*0, p_vals, label='Target p(x)', color="C0", alpha=0.3)
    ax.fill_between(x_vals, p_vals, M * q_vals, label='M * proposal q(x)', color="lightcoral", alpha=0.3)
    ax.set_ylim(0, M * max(q_vals) * 1.1)
    ax.legend(loc='upper right', bbox_to_anchor=(1.62, 1))
    return scat,

def update(frame):
    x = np.random.uniform(-4, 4)
    y = np.random.uniform(0, M * q(x))
    accept = y <= p(x)
    proposed_x.append(x)
    proposed_y.append(y)
    face_colors.append("#3b4cc0ff" if accept else "#b40426ff")
    offsets = np.column_stack((proposed_x, proposed_y))
    scat.set_offsets(offsets)
    scat.set_facecolors(face_colors)
    return scat,

ani = FuncAnimation(fig, update, init_func=init, frames=100, interval=100)

plt.title("Rejection Sampling Animation: Standard Gaussian with Uniform Proposal")
plt.xlabel("x")
plt.ylabel("Density")
HTML(ani.to_jshtml())

<IPython.core.display.Javascript object>

In [51]:
import matplotlib
matplotlib.colors.rgb2hex(plt.colormaps["coolwarm"](0), keep_alpha=True)

'#3b4cc0ff'

# Rejection Sampler test on a standard normal distribution

In [ ]:
def gaussian_pdf(x: np.ndarray, mean: float = 0.0, std: float = 1.0) -> np.ndarray:
    """
    Compute the probability density function (PDF) of a Gaussian (normal) distribution.

    Parameters
    ----------
    x : np.ndarray
        Points at which to evaluate the PDF.
    mean : float, optional
        Mean (μ) of the normal distribution. Default is 0.0.
    std : float, optional
        Standard deviation (σ) of the normal distribution. Must be positive. Default is 1.0.

    Returns
    -------
    np.ndarray
        The PDF values of the Gaussian distribution evaluated at each point in `x`.

    """
    coeff = 1 / (std * np.sqrt(2 * np.pi))
    exponent = -((x - mean) ** 2) / (2 * std ** 2)
    return coeff * np.exp(exponent)

In [ ]:
samples, M, acceptance_rate = rejection_sampling_uniform(gaussian_pdf, -4, 4, 1000000, 0, 1)

In [ ]:
print(acceptance_rate)

In [ ]:
xmin, xmax = -4, 4
Z = norm.cdf(xmax) - norm.cdf(xmin)
theoric_acceptance_rate = np.sqrt(2*np.pi) / (Z * (xmax - xmin))
print(theoric_acceptance_rate)

In [ ]:
x = np.linspace(-5, 5, 10000)
pdf = gaussian_pdf(x, 0, 1)
plt.plot(x, pdf, color="black", ls="--", label="Standard Normal density function")
plt.hist(samples, bins=100, density=True, label="Samples from rejection sampler")
plt.axhline(M, color="red", ls=":", label=f"Density Function Maximum: {M:.4f}")
plt.grid(ls="--", alpha=0.5)
plt.legend(loc='upper right', bbox_to_anchor=(1.62, 1))
plt.show()

# Sampling a truncated standard normal distribution

In [ ]:
xmin, xmax = -2, 3
mu, std = 0, 2
pdf = gaussian_pdf(x, mu, std)
official_samples = np.random.normal(mu, std, 1000000)
rejection_samples, M, acceptance_rate = rejection_sampling_uniform(gaussian_pdf, xmin, xmax, 500000, mu, std)

In [ ]:
print(acceptance_rate)

In [ ]:
official_samples = official_samples[(official_samples < xmax) & (official_samples > xmin)]

In [ ]:
def truncated_pdf(x):
    a, b = (xmin - mu) / std, (xmax - mu) / std
    Z = norm.cdf(b) - norm.cdf(a)
    return np.where((x-xmin>0) & (x-xmax<0), pdf / Z, 0)

In [ ]:
samples = {
    "official_samples": official_samples,
    "rejection_samples": rejection_samples
}

for name, sampl in samples.items():
    plt.hist(sampl, bins=100, density=True, alpha=0.5, label=name)
    
plt.plot(x, truncated_pdf(x), color="black", ls="--", label="Truncated standard density")
plt.grid(ls="--", alpha=0.3)
plt.legend(loc='upper right', bbox_to_anchor=(1.6, 1))
plt.show()

Pour la suite  
* Bien amener l'objectif du notebook dans des Markdown  
* Illuster avec une animation le fonctionnement de rejection sampler  
* Comparer le taux d'acceptation selon le proposal  
* Essayer du multimodal  
* Essayer du 2D, 3D, etc pour comparer l'acceptation rate  